In [30]:
import pandas as pd
import numpy as np
import os
import datetime
import matplotlib.pyplot as plt
import yfinance as yf
from scipy.signal import correlate as cr
#adf test
from statsmodels.tsa.stattools import adfuller
#cross correlation
from scipy import signal

#derivate
from sympy import diff, Symbol

Importando dados

In [31]:
#importando dados - INDICADORES
#Ajustar o nome do arquivo
dados_trimestrais = pd.read_csv("C:\\workspace_mestrado\\dados_cvm_trimestrais\\base_dados_tri_2024.csv", sep=";")
dados_anuais = pd.read_csv("C:\\workspace_mestrado\\dados_cvm_anuais\\base_dados_2024.csv", sep=";")

Tratamento de dados

In [32]:
#filtro inicial
def filtro_inicial(dados : pd.DataFrame,  empresa: int) -> pd.DataFrame:

    #cd_cvm= dados[dados['DENOM_CIA'] == empresa]['CD_CVM'].unique()[0]
    cd_cvm = empresa
    regex = r"^\d{1}\.\d{2}$"
    
    #filtrar linhas da base_dados_tri que contenham o formato regex
    dados_anuais_regex = dados[dados['CD_CONTA'].str.contains(regex)]
    dados_anuais_filtrados = dados_anuais_regex[['CD_CVM','CD_CONTA', 'ESCALA_MOEDA', 'DT_INI_EXERC','DT_FIM_EXERC','DS_CONTA', 'VL_CONTA', 'ST_CONTA_FIXA']].drop_duplicates()

    dados_anuais_empresa = dados_anuais_filtrados[dados_anuais_filtrados['CD_CVM'] == cd_cvm]
    dados_anuais_empresa['DT_INI_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_INI_EXERC'])
    dados_anuais_empresa['DT_FIM_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_FIM_EXERC'])

        #pegar o CD_CONTA a partir do nome da empresa, para capturar seus dados mesmo que tenha mudado de nome ao longo de sua história

    return dados_anuais_empresa

In [33]:
def compilado_trimestral(dados_trimestrais: pd.DataFrame, dados_anuais: pd.DataFrame):
    dados_trimestrais_copia = dados_trimestrais.copy()
    dados_anuais_copia = dados_anuais.copy()
    dados_3tri = dados_trimestrais_copia[((dados_trimestrais_copia['DT_FIM_EXERC'] - dados_trimestrais_copia['DT_INI_EXERC']) < datetime.timedelta(days=100)) &
                                         ((dados_trimestrais_copia['DT_FIM_EXERC'] - dados_trimestrais_copia['DT_INI_EXERC']) > datetime.timedelta(days=31))]
    #print(dados_3tri)

    new_data_df = pd.DataFrame(columns=['CD_CVM', 'CD_CONTA', 'ESCALA_MOEDA', 'DT_INI_EXERC', 'DT_FIM_EXERC', 'DS_CONTA', 'VL_CONTA', 'ST_CONTA_FIXA'])
    for ano in range(2011, 2024):
        print({ano})
        resultado_4t = dados_3tri[(dados_3tri['DT_FIM_EXERC'].dt.year == ano)]
        print("Filtro Ano Executado")
        print(resultado_4t['CD_CONTA'])
        
        for cd_conta in resultado_4t['CD_CONTA']:

            print(f"Filtro Conta Executado - {cd_conta}")
            #somando valores dos 3 trimestres
            value_condicao_ano = sum(resultado_4t[(resultado_4t['CD_CONTA'] == cd_conta)]['VL_CONTA'])
            #transformar value_condicao_ano em float
            total_3tri = float(value_condicao_ano)
            print(f"{cd_conta} - Somados 3 trimestres: {total_3tri}")
            
            total_anual = dados_anuais_copia[(dados_anuais_copia['CD_CONTA'] == cd_conta) & (dados_anuais_copia['DT_FIM_EXERC'].dt.year == ano)]['VL_CONTA'].iloc[0]

            value_4t = total_anual - total_3tri
            print(f"value_4t: {value_4t}, total_anual: {total_anual}, total_3tris: {total_3tri}")

            #ADICIONANDO 4 TRIMESTRE NO DATAFRAME
            new_data = {'CD_CVM': [dados_3tri['CD_CVM'].iloc[0]], 'CD_CONTA': [cd_conta], 'ESCALA_MOEDA':  [resultado_4t[(resultado_4t['CD_CONTA'] == cd_conta)]['ESCALA_MOEDA'].iloc[0]],
                        'DT_INI_EXERC': [datetime.datetime(ano, 10, 1)], 'DT_FIM_EXERC': [datetime.datetime(ano, 12, 31)], 'DS_CONTA': [resultado_4t[(resultado_4t['CD_CONTA'] == cd_conta)]['DS_CONTA'].iloc[0]],
                        'VL_CONTA': [value_4t], 'ST_CONTA_FIXA': [resultado_4t[(resultado_4t['CD_CONTA'] == cd_conta)]['ST_CONTA_FIXA'].iloc[0]]}
            
            #transformar new_data em dataframe sendo que cd_vm, cd_conta, escala_moeda, ds_conta e st_conta_fixa são colunas
            new_data_df = pd.concat([pd.DataFrame(new_data_df), pd.DataFrame(new_data)])
            
            #juntar dataframe new_data_df com dados_3tri
        
            #print(f"{cd_conta} - {ano} - Executado")
            print(new_data_df)

            #encerrar todos os loops
        #encerrar todos os loops
        

    
    #exportar dados_3tri para csv
    new_data_df.to_csv("data\\base_dados_trimestres_completos.csv", sep=";")

    dados_trimestrais_completos = pd.concat([dados_3tri, new_data_df], ignore_index=True)
    return dados_trimestrais_completos
    

In [34]:
#2437  - ELETROBRAS 
#18376 - TRANSMISSÃO PAULISTA
#20257 - TAESA
#21490 - ALUPAR
#24120 - ARGO -> IPO EM 2017
dados_empresas = []
for empresa in (2437, 18376, 20257, 21490): 
    
    #concatenar dados_4tri com dados_trimestrais da empresa
    dados_anuais_empresa = filtro_inicial(dados_anuais, empresa)
    dados_trimestrais_empresa = filtro_inicial(dados_trimestrais, empresa)
    dados_trimestrais_completos = compilado_trimestral(dados_trimestrais_empresa, dados_anuais_empresa)
    dados_trimestrais_completos = dados_trimestrais_completos.drop_duplicates()
    dados_trimestrais_completos = dados_trimestrais_completos.sort_values(by=['DT_FIM_EXERC'])
    
    #muda estrutura do dataframe
    #transformar a couna DT_FIM_EXERC no índice, os valores da coluna CD_CONTA em colunas e os valores da coluna VL_CONTA em valores
    dados_trimestrais_completos = dados_trimestrais_completos.pivot(index='DT_FIM_EXERC', columns='CD_CONTA', values='VL_CONTA')
    
    dados_trimestrais_completos.to_csv(f"clean_data\\dados_trimestrais_completos_{empresa}.csv", sep=";")
    print(f"Empresa {empresa} - Dados Exportados")
    #dados_empresas.append(dados_trimestrais_completos)

C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dados_anuais_empresa['DT_INI_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_INI_EXERC'])
C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dados_anuais_empresa['DT_FIM_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_FIM_EXERC'])
C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:13: SettingWithCopyWarning: 
A value is

{2011}
Filtro Ano Executado
0      3.01
1      3.02
5      3.03
6      3.04
24     3.05
25     3.06
28     3.07
29     3.08
32     3.09
33     3.10
36     3.11
39     3.99
43     3.01
45     3.02
47     3.03
49     3.04
91     3.05
93     3.06
99     3.07
101    3.08
107    3.09
109    3.10
115    3.11
121    3.99
127    3.01
129    3.02
131    3.03
133    3.04
175    3.05
177    3.06
205    3.07
207    3.08
213    3.09
215    3.10
221    3.11
227    3.99
Name: CD_CONTA, dtype: object
Filtro Conta Executado - 3.01
3.01 - Somados 3 trimestres: 21516211.0
value_4t: 11545145.0, total_anual: 33061356.0, total_3tris: 21516211.0
  CD_CVM CD_CONTA ESCALA_MOEDA DT_INI_EXERC DT_FIM_EXERC  \
0   2437     3.01          MIL   2011-10-01   2011-12-31   

                                 DS_CONTA    VL_CONTA ST_CONTA_FIXA  
0  Receita de Venda de Bens e/ou Serviços  11545145.0             S  
Filtro Conta Executado - 3.02
3.02 - Somados 3 trimestres: -1127021.0
value_4t: -3588726.0, total_anual: -47

C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dados_anuais_empresa['DT_INI_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_INI_EXERC'])
C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dados_anuais_empresa['DT_FIM_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_FIM_EXERC'])
C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:13: SettingWithCopyWarning: 
A value is

{2011}
Filtro Ano Executado
12005    3.01
12009    3.02
12013    3.03
12015    3.04
12033    3.05
12035    3.06
12041    3.07
12043    3.08
12049    3.09
12051    3.10
12059    3.11
12065    3.99
12072    3.01
12076    3.02
12080    3.03
12082    3.04
12100    3.05
12102    3.06
12108    3.07
12110    3.08
12116    3.09
12118    3.10
12126    3.11
12132    3.99
12138    3.01
12142    3.02
12146    3.03
12148    3.04
12166    3.05
12168    3.06
12174    3.07
12176    3.08
12182    3.09
12184    3.10
12192    3.11
12198    3.99
Name: CD_CONTA, dtype: object
Filtro Conta Executado - 3.01
3.01 - Somados 3 trimestres: 2194307.0
value_4t: 706498.0, total_anual: 2900805.0, total_3tris: 2194307.0
  CD_CVM CD_CONTA ESCALA_MOEDA DT_INI_EXERC DT_FIM_EXERC  \
0  18376     3.01          MIL   2011-10-01   2011-12-31   

                                 DS_CONTA  VL_CONTA ST_CONTA_FIXA  
0  Receita de Venda de Bens e/ou Serviços  706498.0             S  
Filtro Conta Executado - 3.02
3.02 - Somados 

C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dados_anuais_empresa['DT_INI_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_INI_EXERC'])
C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dados_anuais_empresa['DT_FIM_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_FIM_EXERC'])
C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:13: SettingWithCopyWarning: 
A value is

{2011}
Filtro Ano Executado
19805    3.01
19806    3.02
19812    3.03
19813    3.04
19824    3.05
19825    3.06
19828    3.07
19829    3.08
19832    3.09
19833    3.10
19836    3.11
19839    3.99
19847    3.01
19849    3.02
19861    3.03
19863    3.04
19885    3.05
19887    3.06
19893    3.07
19895    3.08
19901    3.09
19903    3.10
19909    3.11
19915    3.99
19929    3.01
19931    3.02
19943    3.03
19945    3.04
19967    3.05
19969    3.06
19975    3.07
19977    3.08
19983    3.09
19985    3.10
19991    3.11
19997    3.99
Name: CD_CONTA, dtype: object
Filtro Conta Executado - 3.01
3.01 - Somados 3 trimestres: 798372.0
value_4t: 198872.0, total_anual: 997244.0, total_3tris: 798372.0
  CD_CVM CD_CONTA ESCALA_MOEDA DT_INI_EXERC DT_FIM_EXERC  \
0  20257     3.01          MIL   2011-10-01   2011-12-31   

                                 DS_CONTA  VL_CONTA ST_CONTA_FIXA  
0  Receita de Venda de Bens e/ou Serviços  198872.0             S  
Filtro Conta Executado - 3.02
3.02 - Somados 3 t

C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dados_anuais_empresa['DT_INI_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_INI_EXERC'])
C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dados_anuais_empresa['DT_FIM_EXERC'] = pd.to_datetime(dados_anuais_empresa['DT_FIM_EXERC'])
C:\Users\giova\AppData\Local\Temp\ipykernel_50828\998522111.py:13: SettingWithCopyWarning: 
A value is

{2011}
Filtro Ano Executado
21266    3.01
21267    3.02
21268    3.03
21269    3.04
21276    3.05
21277    3.06
21280    3.07
21281    3.08
21284    3.09
21285    3.10
21288    3.11
21291    3.99
21356    3.01
21358    3.02
21360    3.03
21362    3.04
21376    3.05
21378    3.06
21384    3.07
21386    3.08
21392    3.09
21394    3.10
21400    3.11
21406    3.99
Name: CD_CONTA, dtype: object
Filtro Conta Executado - 3.01
3.01 - Somados 3 trimestres: 615630.0
value_4t: 598015.0, total_anual: 1213645.0, total_3tris: 615630.0
  CD_CVM CD_CONTA ESCALA_MOEDA DT_INI_EXERC DT_FIM_EXERC  \
0  21490     3.01          MIL   2011-10-01   2011-12-31   

                                 DS_CONTA  VL_CONTA ST_CONTA_FIXA  
0  Receita de Venda de Bens e/ou Serviços  598015.0             S  
Filtro Conta Executado - 3.02
3.02 - Somados 3 trimestres: -199076.0
value_4t: -173975.0, total_anual: -373051.0, total_3tris: -199076.0
  CD_CVM CD_CONTA ESCALA_MOEDA DT_INI_EXERC DT_FIM_EXERC  \
0  21490     3.01 